In [ ]:
import os
import sys
import gensim
import pandas as pd
import numpy as np

from data_processing.data_loader import DataLoader
from data_processing.split_cell import split_cell
from data_processing.preprocess import Preprocess_gene
from data_processing.data import TwitterDataset
%config InlineBackend.figure_format = 'svg'

In [ ]:
#Input the gene expression matrix, with gene names as row names and cell names as column names.
expression_df=pd.read_csv("./example/Multi_P2_data.csv",sep=",",index_col=0)
expression_df

AAACCCACAAAGGAGA-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  \
A1BG                                            0.000000   
A1BG-AS1                                        0.000000   
A1CF                                            0.000000   
A2M                                             1.578796   
A2M-AS1                                         0.000000   
...                                                  ...   
ZYG11A                                          0.000000   
ZYG11B                                          0.000000   
ZYX                                             0.000000   
ZZEF1                                           0.000000   
ZZZ3                                            1.578796   

          AAACCCACAGAGATGC-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  \
A1BG                                            0.000000   
A1BG-AS1                                        0.000000   
A1CF                                            0.000000   
A2M                                             0.570445   
A2M-AS1                                         0.000000   
...                                                  ...   
ZYG11A                                          0.000000   
ZYG11B                                          0.000000   
ZYX                                             0.000000   
ZZEF1                                           0.570445   
ZZZ3                                            0.931418   

          AAACCCAGTAACGGTG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  \
A1BG                                            0.000000   
A1BG-AS1                                        0.000000   
A1CF                                            0.000000   
A2M                                             0.944331   
A2M-AS1                                         0.000000   
...                                                  ...   
ZYG11A                                          0.000000   
ZYG11B                                          0.000000   
ZYX                                             0.000000   
ZZEF1                                           0.944331   
ZZZ3                                            0.000000   

          AAACCCAGTCCAGAAG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  \
A1BG                                                 0.0   
A1BG-AS1                                             0.0   
A1CF                                                 0.0   
A2M                                                  0.0   
A2M-AS1                                              0.0   
...                                                  ...   
ZYG11A                                               0.0   
ZYG11B                                               0.0   
ZYX                                                  0.0   
ZZEF1                                                0.0   
ZZZ3                                                 0.0   

          AAACCCAGTCGTCGGT-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  \
A1BG                                            0.000000   
A1BG-AS1                                        0.000000   
A1CF                                            0.000000   
A2M                                             2.039204   
A2M-AS1                                         0.000000   
...                                                  ...   
ZYG11A                                          0.000000   
ZYG11B                                          0.000000   
ZYX                                             0.000000   
ZZEF1                                           1.171914   
ZZZ3                                            2.039204   

          AAACCCAGTGCTTATG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  \
A1BG                                            0.000000   
A1BG-AS1                                        0.000000   
A1CF                                            0.000000   
A2M                                             2.226923   
A2M-AS1                                         0.000000   
...                                          

In [3]:
obs_df=pd.read_csv("./example/Multi_P2_type.csv",sep=",",index_col=0)
obs_df

Unnamed: 0 cell_type_original  \
0      AAACCCACAAAGGAGA-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1         Fibroblast   
1      AAACCCACAGAGATGC-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1      Cardiomyocyte   
2      AAACCCAGTAACGGTG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1      Cardiomyocyte   
3      AAACCCAGTCCAGAAG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1         Fibroblast   
4      AAACCCAGTCGTCGGT-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1      Cardiomyocyte   
...                                               ...                ...   
18594                        CK174#ACTGCAATCTTACGGA-1        Endothelial   
18595                        CK174#TCGAGCGAGCCTGGTC-1        Endothelial   
18596                        CK174#TACCTCGCAGTTACAC-1      Cardiomyocyte   
18597                        CK174#CAAGGCCAGTCATACC-1      Cardiomyocyte   
18598                        CK174#ATAGGCTTCCGAGGAA-1        Endothelial   

                          cell_type Source  
0      fibroblast of cardiac tissue    RNA  
1           cardiac muscle myoblast    RNA  
2           cardiac muscle myoblast    RNA  
3      fibroblast of cardiac tissue    RNA  
4           cardiac muscle myoblast    RNA  
...                             ...    ...  
18594      cardiac endothelial cell   ATAC  
18595      cardiac endothelial cell   ATAC  
18596       cardiac muscle myoblast   ATAC  
18597       cardiac muscle myoblast   ATAC  
18598      cardiac endothelial cell   ATAC  

[18599 rows x 4 columns]

In [ ]:
#Process the metadata and the corresponding data.
loader1 = DataLoader(expression_matrix_1=expression_df, cell_labels_1=obs_df, top_genes=1000, mode="target",cell_name_column='Unnamed: 0')

ref_dat, ref_label, ref_cell_labels = loader1.process_data()

print("Updated ref_cell_labels:")
print(ref_cell_labels)

更新后的 ref_cell_labels:
                                           Unnamed: 0 cell_type_original  \
0      AAACCCACAAAGGAGA-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1         Fibroblast   
1      AAACCCACAGAGATGC-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1      Cardiomyocyte   
2      AAACCCAGTAACGGTG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1      Cardiomyocyte   
3      AAACCCAGTCCAGAAG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1         Fibroblast   
4      AAACCCAGTCGTCGGT-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1      Cardiomyocyte   
...                                               ...                ...   
18594                        CK174#ACTGCAATCTTACGGA-1        Endothelial   
18595                        CK174#TCGAGCGAGCCTGGTC-1        Endothelial   
18596                        CK174#TACCTCGCAGTTACAC-1      Cardiomyocyte   
18597                        CK174#CAAGGCCAGTCATACC-1      Cardiomyocyte   
18598                        CK174#ATAGGCTTCCGAGGAA-1        Endothelial   

                          cell_type Source  cell_id    mode  
0  

In [ ]:
#Encode genes using the trained w2v model. The default path uses the trained model.
#If you have your own trained w2v vectors, you can add them manually—make sure the version number matches.
preprocess = Preprocess_gene(ref_dat, sen_len=1000)
embedding = preprocess.make_embedding()
gene_name = preprocess.sentence_word2idx()
gene_label = preprocess.labels_to_tensor(ref_label)

Get embedding ...
loading word to vec model ...
get words #84312
total words: 84315


In [ ]:
#Switch the mode to "single" for the application process.
ref_dataset = TwitterDataset(x=gene_name, z=gene_label, mode="single")

In [13]:
from get_result.Get_emb import AlignCell_Emb
from AlignCell import TransformerEncoder, PositionalEncoding, EncoderLayer, FeedForward

In [ ]:
#Use the trained AlignCell model for the cell embedding process.
emb_dat=AlignCell_Emb("./end_multi_omics/FineTurn_no_mtDNA.model")
ref_label, ref_embed=emb_dat.get_embeddings(ref_dataset)

aligncell_emb=emb_dat.generate_dataframe(ref_embed, ref_label, dataset=ref_dataset)
aligncell_emb.index=ref_cell_labels['Unnamed: 0']
aligncell_emb

Processing Dataset: 100%|██████████| 18599/18599 [03:04<00:00, 100.84it/s]


In [ ]:
#Write the aligncell_emb into the object constructed by Scanpy for subsequent dimensionality reduction analysis.
#adata.obsm["AlignCell"] =aligncell_emb.values

In [ ]:
#Use the UMAP parameters in Python for dimensionality reduction and plotting.
#The results may differ slightly from those produced by Scanpy due to different default settings or parameter configurations.
import pandas as pd
import umap
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
reducer = umap.UMAP(n_jobs=1, random_state=1)
umap_embedding = reducer.fit_transform(aligncell_emb)
#Create a new DataFrame to store the results of the dimensionality reduction.
embedding_df = pd.DataFrame(umap_embedding, columns=['UMAP1', 'UMAP2'])
embedding_df['Source'] = ref_cell_labels['Source'].tolist()
embedding_df['Cell_Name'] = ref_cell_labels['Unnamed: 0'].tolist()
embedding_df['Type'] = ref_cell_labels['cell_type_original'].tolist()
embedding_df

/Gao2/dzh/micromamba/envs/deep/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


UMAP1      UMAP2 Source  \
0       8.713036  14.627443    RNA   
1      -3.732249   5.790410    RNA   
2      -3.212431   1.575447    RNA   
3       8.746773  13.521082    RNA   
4       1.167765   1.347371    RNA   
...          ...        ...    ...   
18594  13.307064   1.316783   ATAC   
18595  13.398309  -0.089355   ATAC   
18596   7.122274   3.578547   ATAC   
18597   6.982583   3.371053   ATAC   
18598  13.494649   0.978062   ATAC   

                                            Cell_Name           Type  
0      AAACCCACAAAGGAGA-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1     Fibroblast  
1      AAACCCACAGAGATGC-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  Cardiomyocyte  
2      AAACCCAGTAACGGTG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  Cardiomyocyte  
3      AAACCCAGTCCAGAAG-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1     Fibroblast  
4      AAACCCAGTCGTCGGT-1_1_1_1_1_1_1_1_1_1_1_1_1_1_1  Cardiomyocyte  
...                                               ...            ...  
18594                        CK174#ACTGCAATCTTACGGA-1    Endothelial  
18595                        CK174#TCGAGCGAGCCTGGTC-1    Endothelial  
18596                        CK174#TACCTCGCAGTTACAC-1  Cardiomyocyte  
18597                        CK174#CAAGGCCAGTCATACC-1  Cardiomyocyte  
18598                        CK174#ATAGGCTTCCGAGGAA-1    Endothelial  

[18599 rows x 5 columns]

In [20]:
plt.figure(figsize=(10, 8))
sns.scatterplot(data=embedding_df, x='UMAP1', y='UMAP2', hue='Source', alpha=1, s=10)
plt.title('UMAP projection of DF1 and DF2')
plt.show()

In [21]:
plt.figure(figsize=(10, 8))
sns.scatterplot(data=embedding_df, x='UMAP1', y='UMAP2', hue='Type',alpha=1, s=10)
plt.title('UMAP projection of DF1 and DF2')
plt.show()